<a href="https://colab.research.google.com/github/sarang-manohar/Coursera_Capstone/blob/main/Segmenting%20and%20Clustering%20Neighborhoods%20in%20Toronto.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This notebook puts in the seed of the Capstone Project with Coursera!

In [10]:
import numpy as np
import pandas as pd
import requests
from bs4 import BeautifulSoup
import geocoder
import folium
from pandas.io.json import json_normalize

from geopy.geocoders import Nominatim

print('Libraries imported')

Libraries imported


In [48]:
html_data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')

soup = BeautifulSoup(html_data.text, 'html.parser')
table = soup.find("table",{"rules":"all"})

table_data = []

for row in table.find_all('td'):
    cell = {}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['PostalCode'] = row.p.text[:3]
        cell['Borough'] = (row.span.text).split('(')[0]
        cell['Neighborhood'] = (((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
        table_data.append(cell)

df=pd.DataFrame(table_data)
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})
df['Address'] = df['Borough']+', Toronto, Ontario, Canada, '+df['PostalCode']
df.shape

(103, 4)

In [50]:
lat=[]
long=[]
for i, addr in enumerate(df['Address']):
    with requests.Session() as session:
        print(i,addr)
        g = geocoder.arcgis(addr,session=session)
    lat.append(g.latlng[0])
    long.append(g.latlng[1])

df['Latitude'] = lat
df['Longitude'] = long

df.head()

0 North York, Toronto, Ontario, Canada, M3A


Status code Unknown from https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find: ERROR - HTTPSConnectionPool(host='geocode.arcgis.com', port=443): Read timed out. (read timeout=5.0)


TypeError: 'NoneType' object is not subscriptable

In [16]:
address = 'Toronto, Ontario, Canada'

g = geocoder.arcgis(address)
latitude = g.latlng[0]
longitude = g.latlng[1]
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.648690000000045, -79.38543999999996.


In [30]:
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{} -- {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Toronto) 

map_Toronto

In [31]:
CLIENT_ID = 'Q5LJU1V0DPCB0R5XDREYLILRZGTSPSBFPBX1QGAQHZAAPNPK' # your Foursquare ID
CLIENT_SECRET = 'U4XJXABOBZBSHOWMLEQYHNEYVSXAR0VBAYAUGHLBBQ3LJIVX' # your Foursquare Secret
VERSION = '20210704' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value
ACCESS_TOKEN = '0HUXGDI5F3EDNXPW3RW21KJNV4TB3Z4ITMA34M5VRKXR0HRA'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: Q5LJU1V0DPCB0R5XDREYLILRZGTSPSBFPBX1QGAQHZAAPNPK
CLIENT_SECRET:U4XJXABOBZBSHOWMLEQYHNEYVSXAR0VBAYAUGHLBBQ3LJIVX


In [46]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&GET'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude,ACCESS_TOKEN, VERSION)
results = requests.get(url).json()


Q5LJU1V0DPCB0R5XDREYLILRZGTSPSBFPBX1QGAQHZAAPNPK,U4XJXABOBZBSHOWMLEQYHNEYVSXAR0VBAYAUGHLBBQ3LJIVX,43.648690000000045,-79.38543999999996,0HUXGDI5F3EDNXPW3RW21KJNV4TB3Z4ITMA34M5VRKXR0HRA,20210704


In [33]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

venues = results['response']['venues']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['name', 'categories', 'location.lat', 'location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)
nearby_venues.drop({'categories'},axis=1,inplace=True)
# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

<ipython-input-33-49c1ab2aad27>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


In [34]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

30 venues were returned by Foursquare.


In [47]:
df['Neighborhood'].value_counts()

Malvern, Rouge                                                                                                   1
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale                                           1
Caledonia-Fairbanks                                                                                              1
Little Portugal, Trinity                                                                                         1
Enclave of M5E                                                                                                   1
                                                                                                                ..
Humber Summit                                                                                                    1
Studio District                                                                                                  1
St. James Town                                                                  

In [35]:
venues_list=[]
for name, lat, lng in zip(df['Neighborhood'], df['Latitude'], df['Longitude']):
    print(name)
        
    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        lng, 
        500, 
        LIMIT)
        
    # make the GET request
    results = requests.get(url).json()['response']['groups'][0]['items']
    # return only relevant information for each nearby venue
    venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
    # return only relevant information for each nearby venue
nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
nearby_venues.columns = ['Neighborhood', 
              'Neighborhood Latitude', 
              'Neighborhood Longitude', 
              'Venue', 
              'Venue Latitude', 
              'Venue Longitude', 
              'Venue Category']

nearby_venues.sample(10)


Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Don Mills North
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
The Danforth  East
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmount Park
Bayview Village
Downsview East
The Danforth

Neighborhood  Neighborhood Latitude  \
1297                              Lawrence Park              43.609727   
1568  Kensington Market, Chinatown, Grange Park              43.653510   
622                    Richmond, Adelaide, King              43.649700   
1180                            Studio District              43.658900   
1876     First Canadian Place, Underground city              43.648280   
1049             Commerce Court, Victoria Hotel              43.648400   
760                          The Danforth  East              43.688110   
1951     First Canadian Place, Underground city              43.648280   
687                Dufferin, Dovercourt Village              43.665050   
1324                            York Mills West              43.747780   

      Neighborhood Longitude                               Venue  \
1297              -79.492842                  Lake Crescent Park   
1568              -79.397220              Helena's Magic Kitchen   
622               -79.382580                         Tim Hortons   
1180              -79.348950             Dark Horse Espresso Bar   
1876              -79.381460                           Starbucks   
1049              -79.379140               Toronto Athletic Club   
760               -79.334180          Dieppe Park Sports Complex   
1951              -79.381460                Assembly Chef's Hall   
687               -79.438910  Rosie Robin A Touch Of Convenience   
1324              -79.400330                     Tournament Park   

      Venue Latitude  Venue Longitude     Venue Category  
1297       43.607486       -79.488423               Park  
1568       43.653797       -79.391168         Restaurant  
622        43.646862       -79.382544        Coffee Shop  
1180       43.658498       -79.352356        Coffee Shop  
1876       43.646891       -79.381871        Coffee Shop  
1049       43.647360       -79.381177                Gym  
760        43.692104       -79.336400  Recreation Center  
1951       43.650579       -79.383412         Food Court  
687        43.663182       -79.435427               Café  
1324       43.751257       -79.399717               Park

In [36]:
nearby_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                             
Agincourt                                                           14   
Alderwood, Long Branch                                               4   
Bathurst Manor, Wilson Heights, Downsview North                      1   
Bayview Village                                                      5   
Bedford Park, Lawrence Manor East                                   20   
...                                                                ...   
Willowdale, Newtonbrook                                             21   
Woburn                                                               4   
Woodbine Heights                                                    21   
York Mills West                                                      4   
York Mills, Silver Hills                                             1   

                                                 Neighborhood Longitude  \
Neighborhood                                                              
Agincourt                                                            14   
Alderwood, Long Branch                                                4   
Bathurst Manor, Wilson Heights, Downsview North                       1   
Bayview Village                                                       5   
Bedford Park, Lawrence Manor East                                    20   
...                                                                 ...   
Willowdale, Newtonbrook                                              21   
Woburn                                                                4   
Woodbine Heights                                                     21   
York Mills West                                                       4   
York Mills, Silver Hills                                              1   

                                                 Venue  Venue Latitude  \
Neighborhood                                                             
Agincourt                                           14              14   
Alderwood, Long Branch                               4               4   
Bathurst Manor, Wilson Heights, Downsview North      1               1   
Bayview Village                                      5               5   
Bedford Park, Lawrence Manor East                   20              20   
...                                                ...             ...   
Willowdale, Newtonbrook                             21              21   
Woburn                                               4               4   
Woodbine Heights                                    21              21   
York Mills West                                      4               4   
York Mills, Silver Hills                             1               1   

                                                 Venue Longitude  \
Neighborhood                                                       
Agincourt                                                     14   
Alderwood, Long Branch                                         4   
Bathurst Manor, Wilson Heights, Downsview North                1   
Bayview Village                                                5   
Bedford Park, Lawrence Manor East                             20   
...                                                          ...   
Willowdale, Newtonbrook                                       21   
Woburn                                                         4   
Woodbine Heights                                              21   
York Mills West                                                4   
York Mills, Silver Hills                                       1   

                                                 Venue Category  
Neighborhood                                                     
Agincourt                                                    14  
Alderwood, Long Branch                                        4 

In [41]:
print('There are {} uniques categories.'.format(len(nearby_venues['Venue Category'].unique())))

There are 268 uniques categories.


In [42]:
# one hot encoding
toronto_onehot = pd.get_dummies(nearby_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = nearby_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Zoo Exhibit  ATM  \
0                                          Agincourt          0.0  0.0   
1                             Alderwood, Long Branch          0.0  0.0   
2    Bathurst Manor, Wilson Heights, Downsview North          0.0  0.0   
3                                    Bayview Village          0.0  0.0   
4                  Bedford Park, Lawrence Manor East          0.0  0.0   
..                                               ...          ...  ...   
97                           Willowdale, Newtonbrook          0.0  0.0   
98                                            Woburn          0.0  0.0   
99                                  Woodbine Heights          0.0  0.0   
100                                  York Mills West          0.0  0.0   
101                         York Mills, Silver Hills          0.0  0.0   

     American Restaurant  Amphitheater  Antique Shop  Aquarium  Art Gallery  \
0                    0.0           0.0           0.0       0.0          0.0   
1                    0.0           0.0           0.0       0.0          0.0   
2                    0.0           0.0           0.0       0.0          0.0   
3                    0.0           0.0           0.0       0.0          0.0   
4                    0.0           0.0           0.0       0.0          0.0   
..                   ...           ...           ...       ...          ...   
97                   0.0           0.0           0.0       0.0          0.0   
98                   0.0           0.0           0.0       0.0          0.0   
99                   0.0           0.0           0.0       0.0          0.0   
100                  0.0           0.0           0.0       0.0          0.0   
101                  0.0           0.0           0.0       0.0          0.0   

     Art Museum  Arts & Crafts Store  ...  Turkish Restaurant  \
0           0.0                  0.0  ...                 0.0   
1           0.0                  0.0  ...                 0.0   
2           0.0                  0.0  ...                 0.0   
3           0.0                  0.0  ...                 0.0   
4           0.0                  0.0  ...                 0.0   
..          ...                  ...  ...                 ...   
97          0.0                  0.0  ...                 0.0   
98          0.0                  0.0  ...                 0.0   
99          0.0                  0.0  ...                 0.0   
100         0.0                  0.0  ...                 0.0   
101         0.0                  0.0  ...                 0.0   

     Vegetarian / Vegan Restaurant  Video Game Store  Video Store  \
0                              0.0               0.0          0.0   
1                              0.0               0.0          0.0   
2                              0.0               0.0          0.0   
3                              0.0               0.0          0.0   
4                              0.0               0.0          0.0   
..                             ...               ...          ...   
97                             0.0               0.0          0.0   
98                             0.0               0.0          0.0   
99                             0.0               0.0          0.0   
100                            0.0               0.0          0.0   
101                            0.0               0.0          0.0   

     Vietnamese Restaurant  Wine Bar  Wine Shop  Wings Joint  Women's Store  \
0                 0.071429       0.0        0.0          0.0            0.0   
1                 0.000000       0.0        0.0          0.0            0.0   
2                 0.000000       0.0        0.0          0.0            0.0   
3                 0.000000       0.0        0.0          0.0            0.0   
4                 0.000000       0.0        0.0          0.0            0.0   
..                     ...       ...        ...          ...            ...   
97                0.000000       0.0   

In [18]:
df_crime = pd.read_csv(r'../data/crime_report.csv'); df_crime.head()

X          Y  Index_ event_unique_id            occurrencedate  \
0 -79.405228  43.656982    7801  GO-20152165447  2015-12-18T03:58:00.000Z   
1 -79.307907  43.778732    7802  GO-20151417245  2015-08-15T21:45:00.000Z   
2 -79.225029  43.765942    7803  GO-20151421107  2015-08-16T16:00:00.000Z   
3 -79.140823  43.778648    7804  GO-20152167714  2015-11-26T13:00:00.000Z   
4 -79.288361  43.691235    7805  GO-20152169954  2015-12-18T19:50:00.000Z   

               reporteddate premisetype  ucr_code  ucr_ext  offence  ...  \
0  2015-12-18T03:59:00.000Z  Commercial      1430      100  Assault  ...   
1  2015-08-17T22:11:00.000Z  Commercial      1430      100  Assault  ...   
2  2015-08-18T14:40:00.000Z   Apartment      2120      200      B&E  ...   
3  2015-12-18T13:38:00.000Z       Other      2120      200      B&E  ...   
4  2015-12-18T19:55:00.000Z  Commercial      1430      100  Assault  ...   

   occurrencedayofyear occurrencedayofweek  occurrencehour              MCI  \
0                352.0          Friday                   3          Assault   
1                227.0          Saturday                21          Assault   
2                228.0          Sunday                  16  Break and Enter   
3                330.0          Thursday                13  Break and Enter   
4                352.0          Friday                  19          Assault   

  Division  Hood_ID                 Neighbourhood       Long        Lat  \
0      D14       79               University (79) -79.405228  43.656982   
1      D42      118  Tam O'Shanter-Sullivan (118) -79.307907  43.778732   
2      D43      137                  Woburn (137) -79.225029  43.765942   
3      D43      133  Centennial Scarborough (133) -79.140823  43.778648   
4      D55       61            Taylor-Massey (61) -79.288361  43.691235   

   ObjectId  
0      7001  
1      7002  
2      7003  
3      7004  
4      7005  

[5 rows x 29 columns]

In [29]:
df_crime['Neighbourhood'].value_counts()

Waterfront Communities-The Island (77)    7747
Bay Street Corridor (76)                  6817
Church-Yonge Corridor (75)                6232
West Humber-Clairville (1)                5702
Moss Park (73)                            4786
                                          ... 
Yonge-St.Clair (97)                        412
Guildwood (140)                            411
Maple Leaf (29)                            410
Woodbine-Lumsden (60)                      377
Lambton Baby Point (114)                   353
Name: Neighbourhood, Length: 140, dtype: int64

In [20]:
data = df_crime[['occurrencehour','X','Y']].sort_values('occurrencehour').reset_index().drop('index',axis=1)

data_list=[]

for x in range(0,24):
    data_list.append(data[(data['occurrencehour']==x)][['Y','X']].values.tolist())

data_list

[[[43.6478386, -79.37078859999998],
  [43.6669083, -79.40271],
  [43.654956799999994, -79.37587739999998],
  [43.662571, -79.4433365],
  [43.7044754, -79.5042496],
  [43.6339531, -79.43477630000001],
  [43.6657372, -79.491188],
  [43.6537323, -79.3732529],
  [43.6722717, -79.4720459],
  [43.6746826, -79.431488],
  [43.7849655, -79.1681061],
  [43.7305527, -79.5698242],
  [43.7305527, -79.5698242],
  [43.6873589, -79.5718002],
  [43.66539, -79.409996],
  [43.62854, -79.4991074],
  [43.8047791, -79.2848816],
  [43.7393761, -79.42386630000001],
  [43.7041321, -79.2999802],
  [43.7412415, -79.5136871],
  [43.6704216, -79.4492493],
  [43.7681923, -79.3884125],
  [43.7827454, -79.23426820000002],
  [43.6573067, -79.3734589],
  [43.64465710000001, -79.5307999],
  [43.7462997, -79.1987457],
  [43.6524124, -79.367424],
  [43.7403069, -79.43580630000001],
  [43.6572304, -79.4668503],
  [43.7885361, -79.4504471],
  [43.7819366, -79.3914948],
  [43.6491318, -79.37219240000002],
  [43.6722145, -79.

In [21]:
import folium.plugins as plugins

heatmap = plugins.HeatMapWithTime(data_list,radius=5).add_to(map_Toronto)

map_Toronto
